In [1]:
import os
import sys
import time
import logging
import datetime
import argparse

home_dir = os.path.abspath(os.getcwd()+"/../")
sys.path.append(home_dir)
home_dir = os.path.abspath(os.getcwd())
sys.path.append(home_dir)
print(home_dir)

from pprint import pprint
from mpi4py import MPI
import numpy as np

import torch
from detectron2.data import MetadataCatalog
from detectron2.utils.logger import log_every_n_seconds

from utils.arguments import load_opt_command
from utils.distributed import init_distributed, is_main_process, apply_distributed, synchronize
from utils.misc import hook_metadata, hook_switcher, hook_opt
from datasets import build_evaluator, build_eval_dataloader
from xdecoder import build_model
from xdecoder.BaseModel import BaseModel
from xdecoder.utils import get_class_names

# logger = logging.getLogger(__name__)
# logging.basicConfig(level = logging.INFO)

from utils.arguments import load_opt_from_config_files, load_config_dict_to_opt

/home/djjin/Mygit/X-Decoder/notebooks


Invalid MIT-MAGIC-COOKIE-1 key

AttributeError: module 'PIL.Image' has no attribute 'LINEAR'

In [ ]:
parser = argparse.ArgumentParser(description='Pretrain or fine-tune models for NLP tasks.')
parser.add_argument('--command', default="evaluate", help='Command: train/evaluate/train-and-evaluate')
parser.add_argument('--conf_files', nargs='+', help='Path(s) to the config file(s).')
parser.add_argument('--user_dir', help='Path to the user defined module for tasks (models, criteria), optimizers, and lr schedulers.')
parser.add_argument('--config_overrides', nargs='*', help='Override parameters on config with a json style string, e.g. {"<PARAM_NAME_1>": <PARAM_VALUE_1>, "<PARAM_GROUP_2>.<PARAM_SUBGROUP_2>.<PARAM_2>": <PARAM_VALUE_2>}. A key with "." updates the object in the corresponding nested dict. Remember to escape " in command line.')
parser.add_argument('--overrides', help='arguments that used to override the config file in cmdline', nargs=argparse.REMAINDER)

cmdline_args = parser.parse_args('')
cmdline_args.conf_files = [os.path.join(home_dir, "../configs/xdecoder/svlp_focalt_lang.yaml")]
cmdline_args.overrides = ['WEIGHT', '../checkpoints/xdecoder_focalt_best_openseg.pt'] 
cmdline_args.overrides

['WEIGHT', '../checkpoints/xdecoder_focalt_best_openseg.pt']

In [ ]:

opt = load_opt_from_config_files(cmdline_args.conf_files)

keys = [cmdline_args.overrides[idx*2] for idx in range(len(cmdline_args.overrides)//2)]
vals = [cmdline_args.overrides[idx*2+1] for idx in range(len(cmdline_args.overrides)//2)]
vals = [val.replace('false', '').replace('False','') if len(val.replace(' ', '')) == 5 else val for val in vals]
types = []
for key in keys:
    key = key.split('.')
    ele = opt.copy()
    while len(key) > 0:
        ele = ele[key.pop(0)]
    types.append(type(ele))

config_dict = {x:z(y) for x,y,z in zip(keys, vals, types)}
config_dict

load_config_dict_to_opt(opt, config_dict)
for key, val in cmdline_args.__dict__.items():
    if val is not None:
        opt[key] = val

opt = init_distributed(opt)

In [ ]:
pprint(opt)

{'ADE20K': {'DATASET': {'DATASET': 'ade'},
            'INPUT': {'COLOR_AUG_SSD': True,
                      'CROP': {'ENABLED': True,
                               'SINGLE_CATEGORY_MAX_AREA': 1.0,
                               'SIZE': '(640, 640)',
                               'TYPE': 'absolute'},
                      'DATASET_MAPPER_NAME': 'mask_former_panoptic',
                      'FORMAT': 'RGB',
                      'MASK_FORMAT': 'polygon',
                      'MAX_SIZE_TEST': 200,
                      'MAX_SIZE_TRAIN': 200,
                      'MIN_SIZE_TEST': 640,
                      'MIN_SIZE_TRAIN': 640,
                      'MIN_SIZE_TRAIN_SAMPLING': 'choice',
                      'SIZE_DIVISIBILITY': 640},
            'TEST': {'BATCH_SIZE_TOTAL': 8}},
 'BDD': {'DATALOADER': {'ASPECT_RATIO_GROUPING': False,
                        'FILTER_EMPTY_ANNOTATIONS': False,
                        'LOAD_PROPOSALS': False,
                        'NUM_WORKERS': 0,
 

In [ ]:
# model = BaseModel(opt, build_model(opt)).from_pretrained(opt['WEIGHT']).eval().cuda()

## ade20k_panoptic_val

In [ ]:
from datasets.build import get_config_from_name
cfg = get_config_from_name(opt, 'refcoco')
dataset_name = cfg['DATASETS']['TEST']


In [ ]:
from datasets.build import get_detection_dataset_dicts
datasets = get_detection_dataset_dicts(dataset_name[0])
datasets

[{'file_name': '../datasets/coco/images/train2017/000000147459.jpg',
  'image_id': 147459,
  'grounding_info': [{'segmentation': [[372.05,
      95.71,
      372.05,
      95.71,
      353.39,
      108.54,
      352.22,
      117.87,
      356.89,
      131.87,
      366.22,
      147.03,
      380.21,
      158.69,
      372.05,
      176.19,
      363.88,
      197.18,
      366.22,
      214.68,
      358.05,
      228.67,
      344.06,
      243.83,
      313.73,
      265.99,
      302.07,
      268.32,
      300.9,
      285.82,
      313.73,
      290.48,
      318.4,
      282.32,
      325.4,
      276.49,
      331.23,
      268.32,
      359.22,
      260.16,
      380.21,
      241.5,
      391.87,
      225.17,
      411.7,
      250.83,
      411.7,
      254.33,
      393.04,
      258.99,
      376.71,
      260.16,
      353.39,
      269.49,
      340.56,
      286.99,
      346.39,
      340.64,
      368.55,
      390.79,
      365.05,
      407.11,
      352.22,
 

In [ ]:
dataloaders = build_eval_dataloader(opt)
dataloaders

{'WEIGHT': '../checkpoints/xdecoder_focalt_best_openseg.pt', 'PORT': 53711, 'VERBOSE': True, 'SAVE_DIR': '../../data/output/test', 'MODEL': {'NAME': 'xdecoder_model', 'HEAD': 'xdecoder_head', 'MASK_ON': False, 'KEYPOINT_ON': False, 'LOAD_PROPOSALS': False, 'DIM_PROJ': 512, 'BACKBONE_DIM': 768, 'TEXT': {'ARCH': 'vlpencoder', 'NAME': 'transformer', 'TOKENIZER': 'clip', 'CONTEXT_LENGTH': 77, 'WIDTH': 512, 'HEADS': 8, 'LAYERS': 12, 'AUTOGRESSIVE': True}, 'BACKBONE': {'NAME': 'focal_dw', 'PRETRAINED': '', 'LOAD_PRETRAINED': False, 'FOCAL': {'PRETRAIN_IMG_SIZE': 224, 'PATCH_SIZE': 4, 'EMBED_DIM': 96, 'DEPTHS': [2, 2, 6, 2], 'FOCAL_LEVELS': [3, 3, 3, 3], 'FOCAL_WINDOWS': [3, 3, 3, 3], 'DROP_PATH_RATE': 0.3, 'MLP_RATIO': 4.0, 'DROP_RATE': 0.0, 'PATCH_NORM': True, 'USE_CONV_EMBED': True, 'SCALING_MODULATOR': True, 'USE_CHECKPOINT': False, 'USE_POSTLN': True, 'USE_POSTLN_IN_MODULATION': False, 'USE_LAYERSCALE': True, 'OUT_FEATURES': ['res2', 'res3', 'res4', 'res5'], 'OUT_INDICES': [0, 1, 2, 3]}}

/home/djjin/anaconda3/envs/conda_X_decoder/lib/python3.9/site-packages/torchvision/transforms/transforms.py:329: UserWarning: Argument 'interpolation' of type int is deprecated since 0.13 and will be removed in 0.15. Please use InterpolationMode enum.
  warnings.warn(


In [ ]:
opt

{'WEIGHT': '../checkpoints/xdecoder_focalt_best_openseg.pt',
 'PORT': 53711,
 'VERBOSE': True,
 'SAVE_DIR': '../../data/output/test',
 'MODEL': {'NAME': 'xdecoder_model',
  'HEAD': 'xdecoder_head',
  'MASK_ON': False,
  'KEYPOINT_ON': False,
  'LOAD_PROPOSALS': False,
  'DIM_PROJ': 512,
  'BACKBONE_DIM': 768,
  'TEXT': {'ARCH': 'vlpencoder',
   'NAME': 'transformer',
   'TOKENIZER': 'clip',
   'CONTEXT_LENGTH': 77,
   'WIDTH': 512,
   'HEADS': 8,
   'LAYERS': 12,
   'AUTOGRESSIVE': True},
  'BACKBONE': {'NAME': 'focal_dw',
   'PRETRAINED': '',
   'LOAD_PRETRAINED': False,
   'FOCAL': {'PRETRAIN_IMG_SIZE': 224,
    'PATCH_SIZE': 4,
    'EMBED_DIM': 96,
    'DEPTHS': [2, 2, 6, 2],
    'FOCAL_LEVELS': [3, 3, 3, 3],
    'FOCAL_WINDOWS': [3, 3, 3, 3],
    'DROP_PATH_RATE': 0.3,
    'MLP_RATIO': 4.0,
    'DROP_RATE': 0.0,
    'PATCH_NORM': True,
    'USE_CONV_EMBED': True,
    'SCALING_MODULATOR': True,
    'USE_CHECKPOINT': False,
    'USE_POSTLN': True,
    'USE_POSTLN_IN_MODULATION': Fals

In [ ]:
dataset_names = opt['DATASETS']['TEST']

In [ ]:
opt['TEST']

{'BATCH_SIZE_TOTAL': 8}

In [ ]:
for dataloader, dataset_name in zip(dataloaders, dataset_names):
    # build evaluator
    evaluator = build_evaluator(opt, dataset_name, opt['SAVE_DIR'])
    evaluator.reset()
    with torch.no_grad():
        for idx, batch in enumerate(dataloader):
            if idx == 1:
                break
            for test in batch:
                pass
            # forward
            with torch.autocast(device_type='cuda', dtype=torch.float16):
                outputs = model(batch, mode=eval_type)
            print(outputs)

KeyboardInterrupt: 